In [ ]:
!pip install pytorch-crf

In [ ]:
import wandb
wandb.login()

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: laiducaivn (laiducaivn-fpt-university) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


True

# Data Preparation

In [ ]:
import pandas as pd

splits = {'train': 'data/train-00000-of-00001-b0417886a268b83a.parquet', 'valid': 'data/valid-00000-of-00001-846411c236133ba3.parquet'}
df_train = pd.read_parquet("hf://datasets/datnth1709/VLSP2016-NER-data/" + splits["train"])
df_valid = pd.read_parquet("hf://datasets/datnth1709/VLSP2016-NER-data/" + splits["valid"])
df = pd.concat([df_train, df_valid]).reset_index(drop=True)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [ ]:
# Tạo thêm các cột khác
def join_tokens(tokens):
    text = ' '.join(tokens)
    return text

def reform_raw_text(tokens):
    text = ' '.join(tokens)
    return text.replace("_", " ")

def label(x):
  return [id_tag[int(i)] for i in x]

def replace_7_8(lst):
    return [0 if x in (7, 8) else x for x in lst]


tag_id = {'O': 0, 'B-PER': 1, 'I-PER': 2, 'B-ORG': 3, 'I-ORG': 4, 'B-LOC': 5, 'I-LOC': 6}
id_tag = {0: 'O', 1: 'B-PER', 2: 'I-PER', 3: 'B-ORG', 4: 'I-ORG', 5: 'B-LOC', 6: 'I-LOC'}


df['ner_tags'] = df['ner_tags'].apply(replace_7_8)
df['text_withseg'] = df['tokens'].apply(join_tokens)
df['text_raw'] = df['tokens'].apply(reform_raw_text)
df["ner_labels"] = df.ner_tags.apply(label)
df.columns = ['tokens', 'id', 'seg_text', 'raw_text', 'labels']
df


tokens  \
0                        [Không_khí, thật, náo_nhiệt, .]   
1      [Chị, Lãnh, và, Xăng, ra, đi, ,, mình, đứng, n...   
2      [Suy_tính, mãi, ,, khóc, mãi, rồi, Phúc, lấy, ...   
3      [Hoà, bảo, hồi, mới, qua, đâu, có, biết, nấu_n...   
4                         [Nhật_ký, của, thuyền_viên, .]   
...                                                  ...   
16853  [Nghe, thấy, đã, ghê_ghê, nhưng, Nhiêu, chưa, ...   
16854        [Nhưng, mọi, chuyện, không, dừng, ở, đó, .]   
16855  [Hoà, bảo, thời_gian, đầu, mặc_cảm, lắm, ,, ở,...   
16856  [Biết_bao, người, đã, tình_nguyện, hiến_dâng, ...   
16857  [Trên, đây, mới, là, “, thành_tích, ”, tiêu, t...   

                                                      id  \
0                                           [0, 0, 0, 0]   
1      [0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2      [0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, ...   
3      [1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 0, ...   
4                                           [0, 0, 0, 0]   
...                                                  ...   
16853  [0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, ...   
16854                           [0, 0, 0, 0, 0, 0, 0, 0]   
16855  [1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
16856      [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
16857  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                                seg_text  \
0                             Không_khí thật náo_nhiệt .   
1      Chị Lãnh và Xăng ra đi , mình đứng nhìn hai ch...   
2      Suy_tính mãi , khóc mãi rồi Phúc lấy ra tờ giấ...   
3      Hoà bảo hồi mới qua đâu có biết nấu_nướng gì ,...   
4                              Nhật_ký của thuyền_viên .   
...                                                  ...   
16853  Nghe thấy đã ghê_ghê nhưng Nhiêu chưa được tườ...   
16854                 Nhưng mọi chuyện không dừng ở đó .   
16855  Hoà bảo thời_gian đầu mặc_cảm lắm , ở trong nh...   
16856  Biết_bao người đã tình_nguyện hiến_dâng cả cuộ...   
16857  Trên đây mới là “ thành_tích ” tiêu tiền của m...   

                                                raw_text  \
0                             Không khí thật náo nhiệt .   
1      Chị Lãnh và Xăng ra đi , mình đứng nhìn hai ch...   
2      Suy tính mãi , khóc mãi rồi Phúc lấy ra tờ giấ...   
3      Hoà bảo hồi mới qua đâu có biết nấu nướng gì ,...   
4                              Nhật ký của thuyền viên .   
...                                                  ...   
16853  Nghe thấy đã ghê ghê nhưng Nhiêu chưa được tườ...   
16854                 Nhưng mọi chuyện không dừng ở đó .   
16855  Hoà bảo thời gian đầu mặc cảm lắm , ở trong nh...   
16856  Biết bao người đã tình nguyện hiến dâng cả cuộ...   
16857  Trên đây mới là “ thành tích ” tiêu tiền của m...   

                                                  labels  
0                                           [O, O, O, O]  
1      [O, B-PER, O, B-PER, O, O, O, O, O, O, O, O, O...  
2      [O, O, O, O, O, O, B-PER, O, O, O, O, O, O, O,...  
3      [B-PER, O, O, O, O, O, O, O, O, O, O, O, O, B-...  
4                                           [O, O, O, O]  
...                                                  ...  
16853  [O, O, O, O, O, B-PER, O, O, O, O, O, O, O, O,...  
16854                           [O, O, O, O, O, O, O, O]  
16855  [B-PER, O, O, O, O, O, O, O, O, O, O, O, O, O,...  
16856      [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O]  
16857  [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...  

[16858 rows x 5 columns]

# Get Embedding Vectors

In [ ]:
import torch
from transformers import AutoTokenizer, AutoModel
from tqdm import tqdm

# Load PhoBERT tokenizer và model
tokenizer = AutoTokenizer.from_pretrained("vinai/phobert-base", use_fast=False)
model = AutoModel.from_pretrained("vinai/phobert-base")
model.eval()

config.json:   0%|          | 0.00/557 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/895k [00:00<?, ?B/s]

bpe.codes:   0%|          | 0.00/1.14M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/3.13M [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/543M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/543M [00:00<?, ?B/s]

RobertaModel(
  (embeddings): RobertaEmbeddings(
    (word_embeddings): Embedding(64001, 768, padding_idx=1)
    (position_embeddings): Embedding(258, 768, padding_idx=1)
    (token_type_embeddings): Embedding(1, 768)
    (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (encoder): RobertaEncoder(
    (layer): ModuleList(
      (0-11): 12 x RobertaLayer(
        (attention): RobertaAttention(
          (self): RobertaSdpaSelfAttention(
            (query): Linear(in_features=768, out_features=768, bias=True)
            (key): Linear(in_features=768, out_features=768, bias=True)
            (value): Linear(in_features=768, out_features=768, bias=True)
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (output): RobertaSelfOutput(
            (dense): Linear(in_features=768, out_features=768, bias=True)
            (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
            (dr

In [ ]:
# Hàm gộp các embedding vectors của token bị tách ra khi qua SentencePiece
def group_embeddings(tokens, embeddings):
    word_embeddings = []
    current_vecs = []

    for token, emb in zip(tokens, embeddings):
        if token in ["<s>", "</s>"]:
            continue

        if token.endswith("@@"):
            current_vecs.append(emb)
        else:
            current_vecs.append(emb)
            word_emb = torch.mean(torch.stack(current_vecs), dim=0)
            word_embeddings.append(word_emb)
            current_vecs = []

    if current_vecs:  # Trong trường hợp sót lại cuối câu
        word_emb = torch.mean(torch.stack(current_vecs), dim=0)
        word_embeddings.append(word_emb)

    return word_embeddings

In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

all_embeddings = []  # list of [seq_len_i, 768] tensors
all_labels = [] # list of [seq_len_i,] tensors
len_em = []

# count = 0

for i, row in tqdm(df.iterrows(), total=len(df)):

    # count += 1
    # if count == 500:
    #   break

    # Truy cập phần tử từng dòng
    sentence = row['seg_text']
    gold_labels = row["id"]

    # Cho sentence đi qua SentencePiece
    input_ids = tokenizer.encode(sentence, return_tensors="pt").to(device)

    tokens = tokenizer.convert_ids_to_tokens(input_ids[0].cpu())

    # Encode tạo embeddings
    with torch.no_grad():
        outputs = model(input_ids)
        last_hidden_state = outputs.last_hidden_state.squeeze(0).cpu()

    # Gộp các embeddings đã bị tách khi đi qua SentencePiece
    word_embeds = group_embeddings(tokens, last_hidden_state)

    # Kiểm tra số lượng embeddings và số lượng labels
    if len(word_embeds) != len(gold_labels):
        print(f"Warning: Skipping row {i} - length mismatch")
        continue

    # Thêm vào list tổng / Tới đây là data đã sẵn sàng cho training
    all_embeddings.append(torch.stack(word_embeds))
    all_labels.append(torch.tensor(gold_labels))


  4%|▎         | 626/16858 [00:13<02:41, 100.35it/s]


  4%|▍         | 681/16858 [00:13<02:35, 104.18it/s]


  7%|▋         | 1201/16858 [00:19<02:37, 99.47it/s]


 13%|█▎        | 2206/16858 [00:30<02:26, 100.27it/s]


 15%|█▍        | 2521/16858 [00:33<02:20, 102.24it/s]

...


 90%|████████▉ | 15089/16858 [02:54<00:17, 98.90it/s]


 91%|█████████ | 15336/16858 [02:57<00:15, 99.47it/s] 


 92%|█████████▏| 15453/16858 [02:58<00:14, 94.86it/s]


 92%|█████████▏| 15520/16858 [02:59<00:18, 71.48it/s]


100%|██████████| 16858/16858 [03:14<00:00, 86.65it/s]

# Train CRF with PyTorch

In [ ]:
from torch.utils.data import Dataset, DataLoader

class NERDataset(Dataset):
    def __init__(self, embeddings, labels):
        self.embeddings = embeddings
        self.labels = labels

    def __len__(self):
        return len(self.embeddings)

    def __getitem__(self, idx):
        return self.embeddings[idx], self.labels[idx]

def collate_fn(batch):
    embeddings, labels = zip(*batch)
    lengths = [len(x) for x in embeddings]

    # Padding
    max_len = max(lengths)
    padded_embs = torch.stack([
        torch.cat([e, torch.zeros(max_len - len(e), e.size(1))]) for e in embeddings
    ])
    padded_labels = torch.stack([
        torch.cat([l, torch.full((max_len - len(l),), -1)]) for l in labels
    ])
    return padded_embs, padded_labels, lengths


In [ ]:
from torchcrf import CRF
import torch.nn as nn

class CRFTagger(nn.Module):
    def __init__(self, input_dim, num_tags):
        super().__init__()
        self.hidden2tag = nn.Linear(input_dim, num_tags)
        self.crf = CRF(num_tags, batch_first=True)

    def forward(self, x, labels, mask):
        emissions = self.hidden2tag(x)
        loss = -self.crf(emissions, labels, mask=mask, reduction='mean')
        return loss

    def decode(self, x, mask):
        emissions = self.hidden2tag(x)
        return self.crf.decode(emissions, mask)


In [ ]:
from sklearn.metrics import precision_recall_fscore_support

def evaluate_crf(model, dataloader):
    model.eval()
    all_preds = []
    all_true = []

    with torch.no_grad():
        for x, y, lengths in dataloader:
            mask = (y != -1)
            preds = model.decode(x, mask)

            # Flatten kết quả
            for pred_seq, true_seq, m in zip(preds, y, mask):
                true_seq = true_seq[m].tolist()
                all_preds.extend(pred_seq)
                all_true.extend(true_seq)

    precision, recall, f1, _ = precision_recall_fscore_support(
        all_true, all_preds, average='macro', zero_division=0
    )
    print(f"Precision: {precision:.4f} - Recall: {recall:.4f} - F1: {f1:.4f}")


In [ ]:
from torch.nn.utils.rnn import pad_sequence

# Số nhãn
num_tags = max(label.max().item() for label in all_labels) + 1

# Tạo DataLoader
dataset = NERDataset(all_embeddings, all_labels)
loader = DataLoader(dataset, batch_size=16, shuffle=True, collate_fn=collate_fn)

# Model
model = CRFTagger(input_dim=768, num_tags=num_tags)
optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)

# Training loop
for epoch in range(10):
    model.train()
    total_loss = 0
    for x, y, lengths in loader:
        mask = (y != -1)
        loss = model(x, y, mask)
        total_loss += loss.item()
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
    print(f"Epoch {epoch+1} - Loss: {total_loss:.4f}")
    evaluate_crf(model, loader)


Epoch 1 - Loss: 2298.3390
Precision: 0.8966 - Recall: 0.8211 - F1: 0.8544
Epoch 2 - Loss: 683.3343
Precision: 0.9166 - Recall: 0.8875 - F1: 0.9015
Epoch 3 - Loss: 499.8040
Precision: 0.9242 - Recall: 0.9110 - F1: 0.9172
Epoch 4 - Loss: 410.5207
Precision: 0.9279 - Recall: 0.9250 - F1: 0.9263
Epoch 5 - Loss: 353.9285
Precision: 0.9338 - Recall: 0.9359 - F1: 0.9348
Epoch 6 - Loss: 313.9812
Precision: 0.9372 - Recall: 0.9414 - F1: 0.9392
Epoch 7 - Loss: 285.1696
Precision: 0.9384 - Recall: 0.9420 - F1: 0.9396
Epoch 8 - Loss: 266.1924
Precision: 0.9556 - Recall: 0.9402 - F1: 0.9473
Epoch 9 - Loss: 247.7737
Precision: 0.9590 - Recall: 0.9373 - F1: 0.9475
Epoch 10 - Loss: 233.8348
Precision: 0.9591 - Recall: 0.9446 - F1: 0.9517


In [ ]:
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
from torchcrf import CRF
from torch.nn.utils.rnn import pad_sequence
from sklearn.metrics import precision_recall_fscore_support, classification_report, accuracy_score
from sklearn.model_selection import train_test_split
from tqdm import tqdm
import wandb
import os

# Initialize Weights & Biases
wandb.init(
    project="NER",
    name="CRF_VLSP2016",
    config={
        "epochs": 20,
        "batch_size": 16,
        "learning_rate": 1e-3,
        "input_dim": 768,
        "test_size": 0.2
    }
)
config = wandb.config

# Prepare train/test split
train_embs, test_embs, train_labels, test_labels = train_test_split(
    all_embeddings, all_labels,
    test_size=config.test_size,
    random_state=42
)

class NERDataset(Dataset):
    def __init__(self, embeddings, labels):
        self.embeddings = embeddings
        self.labels = labels

    def __len__(self):
        return len(self.embeddings)

    def __getitem__(self, idx):
        return self.embeddings[idx], self.labels[idx]


def collate_fn(batch):
    embeddings, labels = zip(*batch)
    lengths = [e.size(0) for e in embeddings]
    max_len = max(lengths)

    padded_embs = torch.stack([
        torch.cat([e, torch.zeros(max_len - e.size(0), e.size(1))]) for e in embeddings
    ])
    padded_labels = torch.stack([
        torch.cat([l, torch.full((max_len - l.size(0),), -1, dtype=torch.long)]) for l in labels
    ])
    return padded_embs, padded_labels, lengths

# Create DataLoaders
train_dataset = NERDataset(train_embs, train_labels)
test_dataset = NERDataset(test_embs, test_labels)
train_loader = DataLoader(train_dataset, batch_size=config.batch_size, shuffle=True, collate_fn=collate_fn)
test_loader = DataLoader(test_dataset, batch_size=config.batch_size, shuffle=False, collate_fn=collate_fn)

# Model setup
num_tags = max(label.max().item() for label in all_labels) + 1
class CRFTagger(nn.Module):
    def __init__(self, input_dim, num_tags):
        super().__init__()
        self.hidden2tag = nn.Linear(input_dim, num_tags)
        self.crf = CRF(num_tags, batch_first=True)

    def forward(self, x, labels, mask):
        emissions = self.hidden2tag(x)
        return -self.crf(emissions, labels, mask=mask, reduction='mean')

    def decode(self, x, mask):
        emissions = self.hidden2tag(x)
        return self.crf.decode(emissions, mask)

model = CRFTagger(input_dim=config.input_dim, num_tags=num_tags)
optimizer = torch.optim.Adam(model.parameters(), lr=config.learning_rate)

# Watch model parameters and gradients
wandb.watch(model, log="all")

# Create checkpoint directory
os.makedirs("checkpoints", exist_ok=True)
best_f1, best_acc = 0.0, 0.0

# Evaluation function with progress bar
def evaluate(model, loader, split_name="Eval"):
    model.eval()
    all_preds, all_true = [], []
    pbar = tqdm(loader, desc=split_name)
    with torch.no_grad():
        for x, y, lengths in pbar:
            mask = (y != -1)
            preds = model.decode(x, mask)
            for pred_seq, true_seq, m in zip(preds, y, mask):
                ts = true_seq[m].tolist()
                all_preds.extend(pred_seq)
                all_true.extend(ts)
    precision, recall, f1, _ = precision_recall_fscore_support(all_true, all_preds, average='macro', zero_division=0)
    acc = accuracy_score(all_true, all_preds)
    return precision, recall, f1, acc

# Training loop
for epoch in range(1, config.epochs + 1):
    model.train()
    total_loss = 0.0
    train_bar = tqdm(train_loader, desc=f"Train Epoch {epoch}/{config.epochs}")
    for batch_idx, (x, y, lengths) in enumerate(train_bar, start=1):
        mask = (y != -1)
        loss = model(x, y, mask)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_loss += loss.item()
        train_bar.set_postfix(batch_loss=loss.item(), avg_loss=total_loss / batch_idx)

    avg_train_loss = total_loss / len(train_loader)
    train_precision, train_recall, train_f1, train_acc = evaluate(model, train_loader, split_name="Train Eval")
    test_precision, test_recall, test_f1, test_acc = evaluate(model, test_loader, split_name="Test Eval")

    # Print & log metrics
    print(f"Epoch {epoch}: loss={avg_train_loss:.4f}, train_f1={train_f1:.4f}, train_acc={train_acc:.4f}, test_f1={test_f1:.4f}, test_acc={test_acc:.4f}")
    wandb.log({
        "epoch": epoch,
        "train_loss": avg_train_loss,
        "train_precision": train_precision,
        "train_recall": train_recall,
        "train_f1": train_f1,
        "train_acc": train_acc,
        "test_precision": test_precision,
        "test_recall": test_recall,
        "test_f1": test_f1,
        "test_acc": test_acc
    })

    # Save best model
    if test_f1 > best_f1 or test_acc > best_acc:
        best_f1 = max(test_f1, best_f1)
        best_acc = max(test_acc, best_acc)
        ckpt_path = f"checkpoints/best_epoch_{epoch}.pt"
        torch.save(model.state_dict(), ckpt_path)
        wandb.save(ckpt_path)
        print(f"Saved improved model to {ckpt_path}")

# Finish W&B run
wandb.finish()



Test Eval: 100%|██████████| 211/211 [00:01<00:00, 160.88it/s]


Epoch 1: loss=2.5528, train_f1=0.8316, train_acc=0.9869, test_f1=0.8319, test_acc=0.9869
Saved improved model to checkpoints/best_epoch_1.pt


Test Eval: 100%|██████████| 211/211 [00:01<00:00, 125.73it/s]


Epoch 2: loss=0.7581, train_f1=0.8833, train_acc=0.9907, test_f1=0.8744, test_acc=0.9903
Saved improved model to checkpoints/best_epoch_2.pt


Test Eval: 100%|██████████| 211/211 [00:01<00:00, 115.40it/s]


...

Epoch 18: loss=0.1728, train_f1=0.9607, train_acc=0.9968, test_f1=0.9039, test_acc=0.9928


Test Eval: 100%|██████████| 211/211 [00:01<00:00, 161.68it/s]


Epoch 19: loss=0.1682, train_f1=0.9664, train_acc=0.9969, test_f1=0.9116, test_acc=0.9929


Test Eval: 100%|██████████| 211/211 [00:01<00:00, 164.59it/s]

Epoch 20: loss=0.1626, train_f1=0.9647, train_acc=0.9969, test_f1=0.9044, test_acc=0.9928


In [ ]:
# Generate final classification report
model.eval()
all_preds, all_true = [], []

with torch.no_grad():
    for x, y, lengths in tqdm(test_loader, desc="Generating classification report"):
        mask = (y != -1)
        preds = model.decode(x, mask)
        for pred_seq, true_seq, m in zip(preds, y, mask):
            ts = true_seq[m].tolist()
            all_preds.extend(pred_seq)
            all_true.extend(ts)

# Generate and print classification report
report = classification_report(all_true, all_preds, digits=4)
print("Classification Report:\n", report)


Generating classification report: 100%|██████████| 211/211 [00:02<00:00, 101.37it/s]

Classification Report:
               precision    recall  f1-score   support

           0     0.9968    0.9983    0.9976     68476
           1     0.9903    0.9754    0.9828      1464
           2     0.9941    0.9781    0.9860       686
           3     0.8384    0.7471    0.7901       257
           4     0.8560    0.7605    0.8054       430
           5     0.9066    0.9073    0.9070      1241
           6     0.8613    0.8628    0.8620       554

    accuracy                         0.9928     73108
   macro avg     0.9205    0.8899    0.9044     73108
weighted avg     0.9927    0.9928    0.9927     73108



In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import shutil
shutil.copy('/content/checkpoints/best_epoch_13.pt', '/content/drive/My Drive')

'/content/drive/My Drive/best_epoch_13.pt'

# Train/Valid/Test

In [ ]:
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
from torchcrf import CRF
from torch.nn.utils.rnn import pad_sequence
from sklearn.metrics import precision_recall_fscore_support, classification_report, accuracy_score
from sklearn.model_selection import train_test_split
from tqdm import tqdm
import wandb
import os

# Initialize Weights & Biases
wandb.init(
    project="NER",
    name="CRF_VLSP2016",
    config={
        "epochs": 20,
        "batch_size": 16,
        "learning_rate": 1e-3,
        # train/val/test ratios
        "train_ratio": 0.70,
        "val_ratio": 0.15,
        "test_ratio": 0.15
    }
)
config = wandb.config

# Create splits: first separate out test, then train/val
emb_train_val, emb_test, lbl_train_val, lbl_test = train_test_split(
    all_embeddings, all_labels,
    test_size=config.test_ratio,
    random_state=42
)
# Compute validation size relative to remaining (val_ratio / (train_ratio + val_ratio))
val_relative = config.val_ratio / (config.train_ratio + config.val_ratio)
emb_train, emb_val, lbl_train, lbl_val = train_test_split(
    emb_train_val, lbl_train_val,
    test_size=val_relative,
    random_state=42
)

class NERDataset(Dataset):
    def __init__(self, embeddings, labels):
        self.embeddings = embeddings
        self.labels = labels

    def __len__(self):
        return len(self.embeddings)

    def __getitem__(self, idx):
        return self.embeddings[idx], self.labels[idx]


def collate_fn(batch):
    embeddings, labels = zip(*batch)
    lengths = [e.size(0) for e in embeddings]
    max_len = max(lengths)

    padded_embs = torch.stack([
        torch.cat([e, torch.zeros(max_len - e.size(0), e.size(1))]) for e in embeddings
    ])
    padded_labels = torch.stack([
        torch.cat([l, torch.full((max_len - l.size(0),), -1, dtype=torch.long)]) for l in labels
    ])
    return padded_embs, padded_labels, lengths

# Create DataLoaders
datasets = {
    'train': NERDataset(emb_train, lbl_train),
    'val': NERDataset(emb_val, lbl_val),
    'test': NERDataset(emb_test, lbl_test)
}
loaders = {
    split: DataLoader(ds, batch_size=config.batch_size,
                       shuffle=(split=='train'), collate_fn=collate_fn)
    for split, ds in datasets.items()
}

# Model setup
num_tags = max(label.max().item() for label in all_labels) + 1
class CRFTagger(nn.Module):
    def __init__(self, input_dim, num_tags):
        super().__init__()
        self.hidden2tag = nn.Linear(input_dim, num_tags)
        self.crf = CRF(num_tags, batch_first=True)

    def forward(self, x, labels, mask):
        emissions = self.hidden2tag(x)
        return -self.crf(emissions, labels, mask=mask, reduction='mean')

    def decode(self, x, mask):
        emissions = self.hidden2tag(x)
        return self.crf.decode(emissions, mask)

model = CRFTagger(input_dim=emb_train[0].size(1), num_tags=num_tags)
optimizer = torch.optim.Adam(model.parameters(), lr=config.learning_rate)

# Watch model parameters and gradients
wandb.watch(model, log="all")

# Create checkpoint directory
os.makedirs("checkpoints", exist_ok=True)
best_val_f1 = 0.0

# Evaluation helper
def evaluate(model, loader):
    model.eval()
    all_preds, all_true = [], []
    with torch.no_grad():
        for x, y, _ in loader:
            mask = (y != -1)
            preds = model.decode(x, mask)
            for pred_seq, true_seq, m in zip(preds, y, mask):
                true_labels = true_seq[m].tolist()
                all_preds.extend(pred_seq)
                all_true.extend(true_labels)
    precision, recall, f1, _ = precision_recall_fscore_support(all_true, all_preds, average='macro', zero_division=0)
    acc = accuracy_score(all_true, all_preds)
    return precision, recall, f1, acc

# Training loop
for epoch in range(1, config.epochs + 1):
    model.train()
    total_loss = 0.0
    train_bar = tqdm(loaders['train'], desc=f"Train Epoch {epoch}/{config.epochs}")
    for batch_idx, (x, y, _) in enumerate(train_bar, start=1):
        mask = (y != -1)
        loss = model(x, y, mask)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_loss += loss.item()
        train_bar.set_postfix(batch_loss=loss.item(), avg_loss=total_loss / batch_idx)

    avg_train_loss = total_loss / len(loaders['train'])
    train_precision, train_recall, train_f1, train_acc = evaluate(model, loaders['train'])
    val_precision, val_recall, val_f1, val_acc = evaluate(model, loaders['val'])

    # Print & log metrics for train and val
    print(f"Epoch {epoch}: train_loss={avg_train_loss:.4f}, train_f1={train_f1:.4f}, val_f1={val_f1:.4f}")
    wandb.log({
        "epoch": epoch,
        "train_loss": avg_train_loss,
        "train_precision": train_precision,
        "train_recall": train_recall,
        "train_f1": train_f1,
        "train_acc": train_acc,
        "val_precision": val_precision,
        "val_recall": val_recall,
        "val_f1": val_f1,
        "val_acc": val_acc
    })

    # Save best model based on val_f1
    if val_f1 > best_val_f1:
        best_val_f1 = val_f1
        ckpt_path = f"checkpoints/best_epoch_{epoch}.pt"
        torch.save(model.state_dict(), ckpt_path)
        wandb.save(ckpt_path)
        print(f"Saved improved model to {ckpt_path}")

# Final evaluation on test set
print("Evaluating on test set...")
test_preds, test_true = [], []
model.eval()
with torch.no_grad():
    for x, y, _ in loaders['test']:
        mask = (y != -1)
        preds = model.decode(x, mask)
        for pred_seq, true_seq, m in zip(preds, y, mask):
            test_true.extend(true_seq[m].tolist())
            test_preds.extend(pred_seq)

# Classification report
report_dict = classification_report(test_true, test_preds, output_dict=True)
print(classification_report(test_true, test_preds))

# Log classification report table to wandb
columns = ["label", "precision", "recall", "f1-score", "support"]
rows = []
for label, metrics in report_dict.items():
    if label not in ["accuracy", "macro avg", "weighted avg"]:
        rows.append([label, metrics['precision'], metrics['recall'], metrics['f1-score'], metrics['support']])
# Add overall averages
rows.append(["macro avg", report_dict['macro avg']['precision'], report_dict['macro avg']['recall'], report_dict['macro avg']['f1-score'], report_dict['macro avg']['support']])
rows.append(["weighted avg", report_dict['weighted avg']['precision'], report_dict['weighted avg']['recall'], report_dict['weighted avg']['f1-score'], report_dict['weighted avg']['support']])

table = wandb.Table(columns=columns, data=rows)
wandb.log({"test_classification": table})

# Finish W&B run
wandb.finish()


Train Epoch 1/20: 100%|██████████| 736/736 [00:18<00:00, 39.34it/s, avg_loss=2.91, batch_loss=1.26]


Epoch 1: train_loss=2.9090, train_f1=0.8125, val_f1=0.8168
Saved improved model to checkpoints/best_epoch_1.pt


Train Epoch 2/20: 100%|██████████| 736/736 [00:20<00:00, 35.77it/s, avg_loss=0.835, batch_loss=0.186]


Epoch 2: train_loss=0.8350, train_f1=0.8793, val_f1=0.8784
Saved improved model to checkpoints/best_epoch_2.pt


Train Epoch 3/20: 100%|██████████| 736/736 [00:19<00:00, 37.89it/s, avg_loss=0.6, batch_loss=0.803]


...

Epoch 18: train_loss=0.1747, train_f1=0.9669, val_f1=0.9237


Train Epoch 19/20: 100%|██████████| 736/736 [00:19<00:00, 37.49it/s, avg_loss=0.169, batch_loss=0.0126]


Epoch 19: train_loss=0.1689, train_f1=0.9685, val_f1=0.9231


Train Epoch 20/20: 100%|██████████| 736/736 [00:20<00:00, 36.24it/s, avg_loss=0.164, batch_loss=0.252]


Epoch 20: train_loss=0.1635, train_f1=0.9719, val_f1=0.9237
Evaluating on test set...
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     51036
           1       0.99      0.98      0.99      1112
           2       0.98      0.99      0.99       506
           3       0.83      0.77      0.80       180
           4       0.83      0.73      0.78       291
           5       0.89      0.91      0.90       939
           6       0.86      0.85      0.85       428

    accuracy                           0.99     54492
   macro avg       0.91      0.89      0.90     54492
weighted avg       0.99      0.99      0.99     54492



# Train CRF With Kerras

In [ ]:
import numpy as np
from tensorflow.keras.preprocessing.sequence import pad_sequences

X = [emb.numpy() for emb in all_embeddings]
y = [label.numpy() for label in all_labels]

max_len = max(len(seq) for seq in X)
num_tags = max(label.max().item() for label in all_labels) + 1

X_padded = pad_sequences(X, maxlen=max_len, dtype='float32', padding='post')
y_padded = pad_sequences(y, maxlen=max_len, value=-1)


In [ ]:
import tensorflow as tf
import tensorflow_addons as tfa
from tensorflow.keras import layers, Model, Input

input_dim = X_padded.shape[2]

inputs = Input(shape=(max_len, input_dim), name="input_embedding")
masking = layers.Masking(mask_value=0.0)(inputs)
dense = layers.Dense(num_tags)(masking)

# CRF Layer
crf = tfa.layers.CRF(num_tags)
outputs = crf(dense)

model = Model(inputs=inputs, outputs=outputs)
model.compile(optimizer='adam', loss=crf.loss, metrics=[crf.accuracy])
model.summary()


In [ ]:
model.fit(
    X_padded, y_padded,
    batch_size=32,
    epochs=5,
    validation_split=0.1,
    verbose=1
)


In [ ]:
pred = model.predict(X_padded)
pred_labels = np.argmax(pred, axis=-1)

from sklearn.metrics import classification_report

y_true_flat = []
y_pred_flat = []

for i in range(len(y_padded)):
    for j in range(max_len):
        if y_padded[i][j] != -1:
            y_true_flat.append(y_padded[i][j])
            y_pred_flat.append(pred_labels[i][j])

print(classification_report(y_true_flat, y_pred_flat, digits=4))


# Train Random Forest

In [ ]:
import torch
import numpy as np
from sklearn.model_selection import train_test_split

X_flat = []
y_flat = []

for emb_seq, label_seq in zip(all_embeddings, all_labels):
    for emb, label in zip(emb_seq, label_seq):
        X_flat.append(emb.numpy())   # emb: [768]
        y_flat.append(label.item())  # label: int

X_flat = np.array(X_flat)  # [N, 768]
y_flat = np.array(y_flat)  # [N]


In [ ]:
print(X_flat.shape)
print(y_flat.shape)

(368172, 768)
(368172,)


In [ ]:
# Kiểm tra độ lệch data
unique_values, counts = np.unique(y_flat, return_counts=True)

# In ra từng giá trị và số lần xuất hiện
for val, count in zip(unique_values, counts):
    print(f"Label {val}: {count} times")


Label 0: 344986 times
Label 1: 7450 times
Label 2: 3504 times
Label 3: 1204 times
Label 4: 2050 times
Label 5: 6211 times
Label 6: 2767 times


In [ ]:
X_train, X_test, y_train, y_test = train_test_split(
    X_flat, y_flat, test_size=0.2, random_state=42, stratify=y_flat)


In [ ]:
import lightgbm as lgb
from sklearn.metrics import accuracy_score, f1_score, classification_report

# Khởi tạo wandb project
wandb.init(project="NER", name="RandomForest_100Trees_VLSP2016")

# Tạo Dataset cho LightGBM
train_data = lgb.Dataset(X_train, label=y_train)
test_data = lgb.Dataset(X_test, label=y_test, reference=train_data)

# Cấu hình tham số LightGBM (Random Forest mode)
params = {
    "objective": "multiclass",          # nếu multiclass classification
    "num_class": len(np.unique(y_train)),
    "metric": "multi_logloss",
    "boosting_type": "rf",              # random forest mode trong LightGBM
    "num_leaves": 31,
    "bagging_freq": 1,
    "bagging_fraction": 0.8,
    "feature_fraction": 0.8,
    "bagging_seed": 42,
    "verbose": -1,
    "seed": 42,
    "is_unbalance": True
}



# Train model, tích hợp wandb callback để log metrics
model = lgb.train(
    params,
    train_data,
    num_boost_round=100,
    valid_sets=[train_data, test_data],
    valid_names=["train", "test"],
    callbacks=[wandb.lightgbm.wandb_callback()]
)

# Dự đoán trên test set
y_pred_prob = model.predict(X_test)
y_pred = np.argmax(y_pred_prob, axis=1)

# Ánh xạ số về nhãn tên entity
label_map = {
    0: 'O',
    1: 'B-PER',
    2: 'I-PER',
    3: 'B-ORG',
    4: 'I-ORG',
    5: 'B-LOC',
    6: 'I-LOC'
}

# Chuyển y_test và y_pred sang nhãn gốc
y_test_labels = [label_map[i] for i in y_test]
y_pred_labels = [label_map[i] for i in y_pred]

# In classification report với nhãn thật
print("\nClassification Report (theo label gốc):")
print(classification_report(y_test_labels, y_pred_labels, digits=4))

# Tạo bảng để log classification report
report_dict = classification_report(y_test_labels, y_pred_labels, output_dict=True)
table = wandb.Table(columns=["Label", "Precision", "Recall", "F1-Score", "Support"])

for label, scores in report_dict.items():
    if isinstance(scores, dict):  # Bỏ các dòng như 'accuracy'
        table.add_data(
            label,
            scores["precision"],
            scores["recall"],
            scores["f1-score"],
            scores["support"]
        )

wandb.log({"Classification Report": table})


# Kết thúc wandb run
wandb.finish()



Classification Report (theo label gốc):
              precision    recall  f1-score   support

       B-LOC     0.4461    0.6167    0.5177      1242
       B-ORG     0.2841    0.6224    0.3901       241
       B-PER     0.5859    0.8423    0.6911      1490
       I-LOC     0.2812    0.6401    0.3907       553
       I-ORG     0.2350    0.4122    0.2994       410
       I-PER     0.6530    0.7489    0.6977       701
           O     0.9914    0.9550    0.9728     68998

    accuracy                         0.9386     73635
   macro avg     0.4967    0.6911    0.5657     73635
weighted avg     0.9589    0.9386    0.9468     73635



# Lưu data

In [ ]:
def save_tensors(all_embeddings, all_labels, embed_path='embeddings.pt', label_path='labels.pt'):
    torch.save(all_embeddings, embed_path)
    torch.save(all_labels, label_path)
    print(f"Saved embeddings to {embed_path} and labels to {label_path}")

In [ ]:
from google.colab import drive
import shutil

# Gọi hàm đã viết
save_tensors(all_embeddings, all_labels)

# Mount và tải lên Drive
drive.mount('/content/drive')
shutil.copy('embeddings.pt', '/content/drive/My Drive')
shutil.copy('labels.pt', '/content/drive/My Drive')


Saved embeddings to embeddings.pt and labels to labels.pt
Mounted at /content/drive


'/content/drive/My Drive/labels.pt'

In [ ]:
model.save_model('lightgbm_rf_model.txt')
shutil.copy('lightgbm_rf_model.txt', '/content/drive/My Drive')

'/content/drive/My Drive/lightgbm_rf_model.txt'